# Machine Exercise 4
### By: Jeryl Salas
We are tasked to create a Conditional Random Field based Named Entity Recognition to identify citations as in the Coleridge Initiative Problem. 

In [106]:
import numpy as np # For computations of probabilities, perplexities and expected count
import os # For folder and file path opening
import json # Used for loading JSON data
import random # For random selection of JSON files for training and testing
import pandas as pd # For transforming JSON data into a pandas dataframe
import nltk # Used for tokenization of training and testing set
from nltk import pos_tag # Used for parts of speech (POS) tagging
from tqdm import tqdm # For displaying progress bar
import re # For regular expression
import itertools # Used in feature extraction to efficiently remove duplicates
from sklearn.preprocessing import OneHotEncoder # Used for converting extracted features to vectors
from sklearn.metrics import accuracy_score, precision_recall_fscore_support # Used for performance metrics
from sklearn.model_selection import train_test_split # Used to split training and testing set
nltk.download('punkt')
nltk.download('averaged_perceptron_tagger_eng') 

[nltk_data] Downloading package punkt to C:\Users\Jeryl
[nltk_data]     Salas\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger_eng to
[nltk_data]     C:\Users\Jeryl Salas\AppData\Roaming\nltk_data...
[nltk_data]   Package averaged_perceptron_tagger_eng is already up-to-
[nltk_data]       date!


True

### A. Loading and Splitting Data

We first load the dataset and the train.csv file. The max sample size of documents would be 4000 with a 60-40 split between training and testing data. The train.csv file would serve as our basis for BIO tagging later. training documents are stored in the "papers" dictionary while test documents are stored in the "test papers" dictionary. Both dictionaries have document ID as the primary key with text as the value

In [107]:
MAX_SAMPLE = 4000
train_path = r'C:\Users\Jeryl Salas\Documents\AI 351\MEx 2 Tokenizer\coleridgeinitiative-show-us-the-data\train.csv'
paper_train_folder = r'C:\Users\Jeryl Salas\Documents\AI 351\MEx 2 Tokenizer\coleridgeinitiative-show-us-the-data\train'

data = pd.read_csv(train_path)
data_extract = data[:MAX_SAMPLE]
train, test = train_test_split(data_extract, test_size=0.4)
print(f'No. raw training rows: {len(train)}')
print(f'No. test rows: {len(test)}')

No. raw training rows: 2400
No. test rows: 1600


In [108]:
train = train.groupby('Id').agg({
    'pub_title': 'first',
    'dataset_title': '|'.join,
    'dataset_label': '|'.join,
    'cleaned_label': '|'.join
}).reset_index()

test = test.groupby('Id').agg({
    'pub_title': 'first',
    'dataset_title': '|'.join,
    'dataset_label': '|'.join,
    'cleaned_label': '|'.join
}).reset_index()

print(f'No. grouped training rows: {len(train)}')
print(f'No. grouped testing rows: {len(test)}')

No. grouped training rows: 2202
No. grouped testing rows: 1517


In [109]:
papers = {}
for paper_id in train['Id'].unique():
    with open(f'{paper_train_folder}\{paper_id}.json', 'r') as f:
        paper = json.load(f)
        papers[paper_id] = paper
        print(f"successfully loaded {paper_id}.JSON")

test_papers = {}
for paper_id in test['Id'].unique():
    with open(f'{paper_train_folder}\{paper_id}.json', 'r') as f:
        paper = json.load(f)
        test_papers[paper_id] = paper
        print(f"successfully loaded test {paper_id}.JSON")

successfully loaded 00243b98-f868-45e4-9b83-0c346c7ecad5.JSON


successfully loaded 00248da3-ac1d-48fa-a95e-cc88553f9583.JSON
successfully loaded 002cbf56-5158-4ec7-83fd-51fa7829bb13.JSON
successfully loaded 0035a1ba-6d1e-487b-bc3d-d49c5d64a3e9.JSON
successfully loaded 0085fd27-7924-41cb-b268-574356c3d6f7.JSON
successfully loaded 00c75e34-3321-4981-8894-58880d3cf6fb.JSON
successfully loaded 01264bbb-9ed7-406d-a189-83fea3e3437c.JSON
successfully loaded 012c83f4-04a0-4939-9680-91f259fb2556.JSON
successfully loaded 01320f4d-0ee7-4baa-8476-167a80a25b69.JSON
successfully loaded 0132ebd3-5a53-460a-9874-2ebd58910177.JSON
successfully loaded 0157bab8-f830-455c-bb4a-5034ebe403c5.JSON
successfully loaded 0168d49e-cbeb-4c4d-ab17-df2181cba61e.JSON
successfully loaded 01a9099f-e71e-48ca-9366-369344844ab1.JSON
successfully loaded 01bc3ff3-859e-4a7a-9d76-28718eef118b.JSON
successfully loaded 01c7c4d7-49bd-436e-8ae8-593b04339c60.JSON
successfully loaded 01cc531e-a911-4880-a7a4-605857bdda42.JSON
successfully loaded 01d71a94-6e85-441c-8381-9c6cd13a800d.JSON
success

### B. Preprocessing Data

For the preprocessing of data, both training and test data will undergro processing such as replacing characters and shortening senntences. As you can see, the BIO tagging functions are here as well which will be used for the next step

In [110]:

def replace_characters(text: str) -> str:
    """
    Replaces specific special characters in the input text according to predefined replacement rules.
    """
    replacement_rules = {'“': '', '”': '', '’': "", '--': '', '(' : '', ')' : '', ',' : '', ';': ''}
    for symbol, replacement in replacement_rules.items():
        text = text.replace(symbol, replacement)
    return text


def shorten_sentences(sentences, MAX_LENGTH=250, OVERLAP=20):
    short_sentences = []
    for sentence in sentences:
        words = sentence.split()
        if len(words) > MAX_LENGTH:
            for p in range(0, len(words), MAX_LENGTH - OVERLAP):
                short_sentences.append(' '.join(words[p:p+MAX_LENGTH]))
        else:
            short_sentences.append(sentence)
    return ''.join(short_sentences)


def preprocess(papers):
    """
    Main preprocessing function used to load and process text data and output tokens for both training and testing
    """

    paper_tokenized_sentences = {}

    for paper_id, text in papers.items():
        all_text = ""
        all_text += text[0]['section_title'] + " " + text[0]['text']
        cleaned_text = replace_characters(all_text.lower())
        shortened_text = shorten_sentences(cleaned_text)

        '''for tokenized_sentence in generate_tokens(shortened_text):
            tokenized_sentences.append(tokenized_sentence)'''
        paper_tokenized_sentences[paper_id] = shortened_text


    print(paper_tokenized_sentences)
    return paper_tokenized_sentences


def find_sublist(big_list, small_list):
    all_positions = []
    for i in range(len(big_list) - len(small_list) + 1):
        if small_list == big_list[i:i+len(small_list)]:
            #print(f"[M] s_l: {small_list}, b_l: {big_list[i:i+len(small_list)]}")
            all_positions.append(i)
        #else:
            #print(f"[NM] s_l: {small_list}, b_l: {big_list[i:i+len(small_list)]}")
    
    return all_positions


def tag_sentence(sentence, labels): 
    sentence_words = sentence.split()
    #print(sentence_words)
    #print(labels)
    
    if labels is not None and any(re.findall(f'\\b{label}\\b', sentence)
                                  for label in labels): 
        nes = ['O'] * len(sentence_words)
        for label in labels:
            label_words = label.split()

            all_pos = find_sublist(sentence_words, label_words)
            for pos in all_pos:
                nes[pos] = 'B'
                for i in range(pos+1, pos+len(label_words)):
                    nes[i] = 'I'

        return True, list(zip(sentence_words, nes))
        
    else: 
        nes = ['O'] * len(sentence_words)
        return False, list(zip(sentence_words, nes))
    

In [111]:
'''for paper_id, text in papers.items():
    print(f"Paper ID: {paper_id}")
    print(f"Text: {text[:200]}...") '''

papers = preprocess(papers)
test_papers = preprocess(test_papers)


{'00243b98-f868-45e4-9b83-0c346c7ecad5': "abstract the investigators used data from the early childhood longitudinal study-kindergarten cohort ecls-k to estimate whether and to what extent the timing and persistence of mathematics difficulties md in kindergarten predicted children's first through fifth grade math growth trajectories. results indicated that children persistently displaying md i.e. those experiencing md in both fall and spring of kindergarten had the lowest subsequent growth rates children with md in spring only had the second-lowest growth rates and children with md in the fall only and who had thus recovered from their md by the spring of kindergarten had the next-lowest growth rates. the children who did not have md in either fall or spring of kindergarten had the highest growth rates. these results were observed prior to and after statistical control for additional variables. they indicate that measuring the timing and persistence of kindergarten children's mathemati

In [112]:
counter = 0
for paper_id, sections in papers.items():
    print(f"Paper ID: {paper_id}")
    print(f"section: {sections}")
    counter += 1
    if counter == 10: break

print("\n\n----------TEST PAPERS-----------\n\n")

counter = 0
for paper_id, sections in test_papers.items():
    print(f"Paper ID: {paper_id}")
    print(f"section: {sections}")
    counter += 1
    if counter == 10: break
    

Paper ID: 00243b98-f868-45e4-9b83-0c346c7ecad5
section: abstract the investigators used data from the early childhood longitudinal study-kindergarten cohort ecls-k to estimate whether and to what extent the timing and persistence of mathematics difficulties md in kindergarten predicted children's first through fifth grade math growth trajectories. results indicated that children persistently displaying md i.e. those experiencing md in both fall and spring of kindergarten had the lowest subsequent growth rates children with md in spring only had the second-lowest growth rates and children with md in the fall only and who had thus recovered from their md by the spring of kindergarten had the next-lowest growth rates. the children who did not have md in either fall or spring of kindergarten had the highest growth rates. these results were observed prior to and after statistical control for additional variables. they indicate that measuring the timing and persistence of kindergarten childr

### C. BIO Tagging and Feature Extraction

After preprocessing, both the training and testing data will undergo BIO tagging and feature extraction. The BIO tagging will serve as the labels, while the extracted features will be used as input data.

#### C.1 BIO Tagging
BIO tagging is a standard approach to **Named Entity Recognition (NER)** that helps capture both the boundaries and the named entity types within text. The tags include:

- **B** = Begin (indicates the beginning of a named entity)
- **I** = Inside (indicates the inside of a named entity)
- **O** = Outside (indicates the word is not part of any named entity)

#### C.2 Feature Extraction
While each word in a sentence is being BIO tagged, it also undergoes feature extraction. The goal is to effectively capture the characteristics of each word, along with its neighboring words. The extracted features include:

1. **Word Identity**  
   - Identity of the word (*w_i*) and its neighboring words

2. **Word Embeddings**  
   - Embeddings for the word (*w_i*) and its neighboring words

3. **Part of Speech (POS)**  
   - POS tag for the word (*w_i*) and its neighboring words

4. **Gazetteer Features**  
   - Presence of the word (*w_i*) in a gazetteer (a curated list of entities)

5. **Prefix and Suffix**  
   - Whether the word (*w_i*) contains a particular prefix or suffix  
   - Prefixes and suffixes are considered from all strings of length ≤ 4

6. **Word Shape**  
   - Full word shape (e.g., capitalized, digits, punctuation) of the word (*w_i*) and its neighboring words

7. **Short Word Shape**  
   - A simplified version of the word shape for the word (*w_i*) and its neighboring words

Reference: https://web.stanford.edu/~jurafsky/slp3/ed3book.pdf

In [113]:
# Initialize POS tags and shape characters
pos_tags_vocabulary = ["<START>", "<END>"] # Special tokens for start and end of a sentence
shape_chars = ['x', '<START>', '<END>', 'X'] # Initialize usual shape characters

def load_glove_embeddings(glove_file):
    '''Load GloVe embeddings from a file and store them in a dictionary'''
    embeddings = {}
    with open(glove_file, 'r', encoding='utf-8') as f:
        for line in f:
            values = line.split()
            word = values[0]
            vector = np.asarray(values[1:], dtype='float32')
            embeddings[word] = vector
    return embeddings


def identity_of_word(word):
    '''Return the identity of the word'''
    return word

def identity_of_neighboring_words(words, i):
    '''Get the identity of neighboring words for a given word in the sentence'''
    prev_word = words[i - 1] if i > 0 else "<START>"
    next_word = words[i + 1] if i < len(words) - 1 else "<END>"
    return prev_word, next_word

def word_embedding(word, embeddings, embedding_dim=200):
    '''Return the embedding vector for a given word using GloVe pre-trained embedding'''
    if word in embeddings:
        return embeddings[word]
    else:
        return np.zeros(embedding_dim)
    
def embedding_of_neighboring_words(words, i, embeddings,  embedding_dim=200):
    '''Get the embedding vectors of neighboring words using GloVe pre-trained embedding'''
    prev_word_embedding = word_embedding(words[i - 1], embeddings) if i > 0 else np.zeros(embedding_dim)
    next_word_embedding = word_embedding(words[i + 1], embeddings) if i < len(words) - 1 else np.zeros(embedding_dim)
    return prev_word_embedding, next_word_embedding

def part_of_speech(word):
    '''Return the Part of Speech (POS) tag for a word'''
    tag = nltk.pos_tag([word])[0][1]

    '''update the POS vocabulary'''
    if tag not in pos_tags_vocabulary:
        pos_tags_vocabulary.append(tag)

    return tag

def pos_of_neighboring_words(words, i):
    '''Get the POS tags of neighboring words'''
    pos_tags = nltk.pos_tag(words)
    prev_pos = pos_tags[i - 1][1] if i > 0 else "<START>"
    next_pos = pos_tags[i + 1][1] if i < len(words) - 1 else "<END>"

    '''Add POS tags to vocabulary in case they don't exist in the POS vocab'''
    if prev_pos not in pos_tags_vocabulary:
        pos_tags_vocabulary.append(prev_pos)

    if next_pos not in pos_tags_vocabulary:
        pos_tags_vocabulary.append(next_pos)

    return prev_pos, next_pos

def word_in_gazetteer(word, gazetteer):
    '''Check if a word exists in the gazetteer which is the dataset_labels in train.csv'''
    return word in gazetteer

def word_prefix(word, length=4):
    '''Extract the prefix of a word up to length 4'''
    return word[:min(len(word), length)]

def word_suffix(word, length=4):
    '''Extract the suffix of a word up to length 4'''
    return word[-min(len(word), length):]

def word_shape(word):
    '''Return the word shape based on the character's characteristics'''
    shape = []
    for char in word:
        if char.isupper():
            shape.append("X") # 'X' for uppercase characters
        elif char.islower():
            shape.append("x") # 'x' for lowercase characters
        elif char.isdigit():
            shape.append("9") # '9' for digits
        else:
            shape.append(char)

    '''Add to shape_chars if they don't exist yet'''
    cat_shape = "".join(shape)
    if cat_shape not in shape_chars:
        shape_chars.append(cat_shape)
    return cat_shape

def shape_of_neighboring_words(words, i):
    '''Get the word shapes of neighboring words'''
    prev_word_shape = word_shape(words[i - 1]) if i > 0 else "<START>"
    next_word_shape = word_shape(words[i + 1]) if i < len(words) - 1 else "<END>"
    return prev_word_shape, next_word_shape

def short_word_shape(word):
    '''Return a shortened version of the word shape (without dupes)'''
    full_shape = word_shape(word)
    short_shape = [k for k, _ in itertools.groupby(full_shape)]  # Remove consecutive duplicates
    '''if short_shape not in shape_chars:
        shape_chars.append(short_shape)'''
    return "".join(short_shape)

def short_shape_of_neighboring_words(words, i):
    '''Return a short shapes of neighboring words'''
    prev_short_shape = short_word_shape(words[i - 1]) if i > 0 else "<START>"
    next_short_shape = short_word_shape(words[i + 1]) if i < len(words) - 1 else "<END>"
    return prev_short_shape, next_short_shape

def gazetteer_features(word, gazetteers):
    '''Check if the word exists in multiple gazetteers'''
    features = {}
    for gaz_name, gaz_list in gazetteers.items():
        features[f"in_{gaz_name}"] = word in gaz_list
    return features

def extract_features(words, i, embeddings, gazetteer):
    '''Extract all features for a given word in a sentence'''
    word = words[i]
    features = {
        "identity": identity_of_word(word),
        "prev_word": identity_of_neighboring_words(words, i)[0],
        "next_word": identity_of_neighboring_words(words, i)[1],
        "embedding": word_embedding(word, embeddings),
        "prev_embedding": embedding_of_neighboring_words(words, i, embeddings)[0],
        "next_embedding": embedding_of_neighboring_words(words, i, embeddings)[1],
        "pos": part_of_speech(word),
        "prev_pos": pos_of_neighboring_words(words, i)[0],
        "next_pos": pos_of_neighboring_words(words, i)[1],
        "in_gazetteer": word_in_gazetteer(word, gazetteer),
        "prefix": word_embedding(word_prefix(word), embeddings),
        "suffix": word_embedding(word_suffix(word), embeddings),
        "word_shape": word_shape(word),
        "prev_word_shape": shape_of_neighboring_words(words, i)[0],
        "next_word_shape": shape_of_neighboring_words(words, i)[1],
        "short_word_shape": short_word_shape(word),
        "prev_short_shape": short_shape_of_neighboring_words(words, i)[0],
        "next_short_shape": short_shape_of_neighboring_words(words, i)[1],
    }
    gaz_features = gazetteer_features(word, gazetteer)
    features.update(gaz_features)
    return features

#### C.3 Tagging and Extraction

In this step, each word from the sentences in both the training and testing sets is tagged and feature-extracted. The process can take around **half an hour** to complete, so we use `tqdm` to display a progress bar for better visibility.

Additionally, the following counters are tracked to show sentence statistics:

- **`cnt_pos`**: Number of sentences containing labels.
- **`cnt_neg`**: Number of sentences without labels.

Example Progress Bar:
[#########......] 60% Complete

As shown in the statistics, there are significantly less cnt_pos for both training and testing sets. This could introduce bias in our CRF training and testing

In [114]:
cnt_pos, cnt_neg = 0, 0 # number of sentences that contain/not contain labels
tcnt_pos, tcnt_neg = 0, 0
ner_data = []
test_ner_data = []
pbar = tqdm(total=len(train))
pbar_test = tqdm(total=len(test))
glove_file = r'C:\Users\Jeryl Salas\Documents\AI 351\glove.6B\glove.6B.200d.txt'
embeddings = load_glove_embeddings(glove_file)
gazetteer = {
    "organization": set(train['dataset_label'].unique())
}
test_gazetteer = {
    "organization": set(test['dataset_label'].unique())
}
all_features = [] 
test_all_features = []


for i, id, dataset_label in train[['Id', 'dataset_label']].itertuples():
    text = papers[id]
    #print(paper)
    
    #print(text)
    sentences = text.split('.')

    cleaned_labels = replace_characters(dataset_label.lower())
    labels = cleaned_labels.split('|')

    for sentence in sentences:
        is_positive, tags = tag_sentence(sentence, labels)
        if is_positive:
            cnt_pos += 1
            ner_data.append(tags)
        else:
            ner_data.append(tags)
            cnt_neg += 1
        
        ner_data[-1]
        
        
        words = sentence.split()
        sentence_features = []
        for i, word in enumerate(words):
            word_features = extract_features(words, i, embeddings, gazetteer)
            sentence_features.append(word_features) 

        all_features.append(sentence_features)
        #print(all_features[-1])

    pbar.update(1)
    pbar.set_description(f"Training data size: {cnt_pos} positives + {cnt_neg} negatives")


for i, id, dataset_label in test[['Id', 'dataset_label']].itertuples():
    text = test_papers[id]
    #print(paper)
    
    #print(text)
    test_sentences = text.split('.')

    cleaned_labels = replace_characters(dataset_label.lower())
    labels = cleaned_labels.split('|')

    for sentence in test_sentences:
        is_positive, tags = tag_sentence(sentence, labels)
        if is_positive:
            tcnt_pos += 1
            test_ner_data.append(tags)
        else:
            test_ner_data.append(tags)
            tcnt_neg += 1
        
        test_ner_data[-1]
        
        
        words = sentence.split()
        sentence_features = []
        for i, word in enumerate(words):
            word_features = extract_features(words, i, embeddings, test_gazetteer)
            sentence_features.append(word_features) 

        test_all_features.append(sentence_features)
        #print(all_features[-1])

    pbar_test.update(1)
    pbar_test.set_description(f"Testing data size: {tcnt_pos} positives + {tcnt_neg} negatives")
                              



Training data size: 181 positives + 20396 negatives: 100%|██████████| 1170/1170 [27:23<00:00,  1.41s/it]
Testing data size: 51 positives + 5803 negatives: 100%|██████████| 299/299 [27:23<00:00,  5.50s/it]




























































































































































































































































































































































































































































































































































































































































































































































































































#### C.4 Write BIO tags in JSON.txt files
The BIO tagged results for both `training` and `test` sets are located at the `ner_json.txt` and `test_ner_json.txt`, respectively.

In [115]:
with open(r'C:\Users\Jeryl Salas\Documents\AI 351\MEx 4 NER with CRF\ner_json.txt', 'w') as f:
    for row in ner_data:
        if row:  # If the row is not empty
            words, nes = list(zip(*row))
            row_json = {'tokens': words, 'tags': nes}
        else:  # If the row is empty
            row_json = {'tokens': "", 'tags': ""}
        
        json.dump(row_json, f)
        f.write('\n')

with open(r'C:\Users\Jeryl Salas\Documents\AI 351\MEx 4 NER with CRF\test_ner_json.txt', 'w') as f:
    for row in test_ner_data:
        if row:  # If the row is not empty
            words, nes = list(zip(*row))
            row_json = {'tokens': words, 'tags': nes}
        else:  # If the row is empty
            row_json = {'tokens': "", 'tags': ""}
        
        json.dump(row_json, f)
        f.write('\n')

In [116]:
print(f"ner structure: {ner_data[0]}")
print(f"feature structure: {all_features[0]}")

ner structure: [('abstract', 'O'), ('the', 'O'), ('investigators', 'O'), ('used', 'O'), ('data', 'O'), ('from', 'O'), ('the', 'O'), ('early', 'O'), ('childhood', 'O'), ('longitudinal', 'O'), ('study-kindergarten', 'O'), ('cohort', 'O'), ('ecls-k', 'O'), ('to', 'O'), ('estimate', 'O'), ('whether', 'O'), ('and', 'O'), ('to', 'O'), ('what', 'O'), ('extent', 'O'), ('the', 'O'), ('timing', 'O'), ('and', 'O'), ('persistence', 'O'), ('of', 'O'), ('mathematics', 'O'), ('difficulties', 'O'), ('md', 'O'), ('in', 'O'), ('kindergarten', 'O'), ('predicted', 'O'), ("children's", 'O'), ('first', 'O'), ('through', 'O'), ('fifth', 'O'), ('grade', 'O'), ('math', 'O'), ('growth', 'O'), ('trajectories', 'O')]
feature structure: [{'identity': 'abstract', 'prev_word': '<START>', 'next_word': 'the', 'embedding': array([-1.8133e-01,  2.0599e-01, -2.0806e-01, -1.6986e-01,  9.1498e-01,
       -1.1684e-02, -4.3782e-01,  5.8944e-01,  1.7412e-01, -3.3781e-01,
       -7.8252e-02, -7.4619e-04,  2.1310e-02,  6.6326e-

### D. Conditional Random Fields (CRF) Model

In this section, we implement a Conditional Random Field (CRF) model. The BIO-tagged data serves as the labels, while the extracted features are used as input data, which is converted into vectors. We leverage `torch` for operations such as `dot`, `logexp`, `randn`, and `matmul`, while `torch.nn` is used to define the model parameters. For model fitting, we apply the Adam optimizer via `torch.optim` to optimize the CRF’s performance. Although `torch` made the implementation easier, the CRF model was still built manually complete with `score computation`, `log likelihood`, `partition function`, and `virterbi algorithm` for decoding.

#### D.1 Feature extraction and BIOS tagging numerical conversion
This function converts linguistic contextual features into vectores by embedding or one-hot encoding. The resulting vector is therefore a concatenation of all the features. It is 1-dimensional of length 6925. This can be represented as:

$$ F_k(X, Y) $$

Where a feature function that maps an entire input sequence $ X $ and an entire output sequence $ Y $ to a feature vector. The feature vector contributes to the final prediction with corresponding weights $ w_k $. Ref: Page 377, Jurafsky, et. Al (2024)

#### D.2 Initialization of CRF
The CRF model initializes with weights and transition weights
   $$
      W \in \mathbb{R}^{|\mathcal{Y}| \times K}
   $$
where $ W[i, k] $ is the weight corresponding to feature $ F_k(X, Y) $ for label $ y_i $.

   $$
   T \in \mathbb{R}^{|\mathcal{Y}| \times |\mathcal{Y}|}
   $$
where $ T[t-1, t] $ is the weight for the transition from label $ Y_{t-1} $ to $ Y_t $.


#### D.3 Forward Pass
The forward pass computes the potential scores for each sequence of labels using dynamic programming (DP),

   $$
   \alpha_0(y) = \mathbf{W}_y \cdot F_k(X_0, Y)
   $$
   where $ \mathbf{x}_0 $ is the feature vector at time $ t=0 $. Using recursion (DP), for each subsequent time step, it computes:
   $$
   \alpha_t(y) = \log \sum_{Y_{t-1}} \exp(\alpha_{t-1}(Y_{t-1}) + \mathbf{T}_{Y_{t-1}, Y}) + \mathbf{W}_y \cdot F_k(X_t, Y)
   $$
   where $ \mathbf{T}_{Y_{t-1}, Y} $ is the transition score from label $ Y_{t-1} $ to $ Y_t $.


#### D.4 Score Computation
This method computes the score of a given sequence of labels. The transition score between successive labels:
$$
\text{score} = \sum_{t=0}^{T-1} \sum_{k=1}^{K} w_k F_k(X_t, Y_t) + \sum_{t=1}^{T-1} \mathbf{T}_{Y_{t-1}, Y_t}
$$


#### D.5 Partition Function
The partition function normalizes the probability distribution over all possible label sequences. It uses the forward pass equation to compute the total score over all possible sequences:



In [130]:
import torch
import torch.nn as nn
import torch.optim as optim

def feature_2_vec(feature, BIOS_tag, pos_tags):
    '''Converts input features into a feature vector'''
    vector = []
    encoder_1 = OneHotEncoder(categories=[pos_tags], sparse_output=False)
    pos_encoder = encoder_1.fit(np.array(pos_tags).reshape(-1, 1))
    pos = pos_encoder.transform(np.array([feature['pos']]).reshape(-1, 1))
    vector.extend(pos[0])

    vector.extend(feature['embedding'].tolist())
    vector.extend(feature['prev_embedding'].tolist())
    vector.extend(feature['next_embedding'].tolist())

    next_pos = pos_encoder.transform(np.array([feature['next_pos']]).reshape(-1, 1))
    prev_pos = pos_encoder.transform(np.array([feature['prev_pos']]).reshape(-1, 1))
    vector.extend(next_pos[0])
    vector.extend(prev_pos[0])

    encoder_3 = OneHotEncoder(categories=[shape_chars], sparse_output=False)
    word_shape_encoder = encoder_3.fit(np.array(shape_chars).reshape(-1, 1))
    next_word_shape_encoder = encoder_3.fit(np.array(shape_chars).reshape(-1, 1))
    #short_word_shape_encoder = encoder_3.fit(np.array(shape_chars).reshape(-1, 1))
    #prev_short_shap_encoder = encoder_3.fit(np.array(shape_chars).reshape(-1, 1))

    word_shape_vector = word_shape_encoder.transform(np.array([feature['word_shape']]).reshape(-1, 1))
    next_word_shape_vector = next_word_shape_encoder.transform(np.array([feature['next_word_shape']]).reshape(-1, 1))
    #short_word_shape_vector = short_word_shape_encoder.transform(np.array([feature['short_word_shape']]).reshape(-1, 1))
    #prev_short_shape_vector = prev_short_shap_encoder.transform(np.array([feature['prev_short_shape']]).reshape(-1, 1))

    vector.extend(feature['prefix'].tolist())
    vector.extend(feature['suffix'].tolist())
    vector.extend(word_shape_vector[0])
    vector.extend(next_word_shape_vector[0])
    #vector.extend(short_word_shape_vector[0])
    #vector.extend(prev_short_shape_vector[0])

    return(vector)

class CRF(nn.Module):
    '''The CRF class'''
    def __init__(self, num_labels, feature_dim):
        super(CRF, self).__init__()
        self.num_labels = num_labels
        self.feature_dim = feature_dim
        self.weights = nn.Parameter(torch.randn(num_labels, feature_dim))
        self.transition_weights = nn.Parameter(torch.randn(num_labels, num_labels))

    '''Compute the log-likelihood for each sequence using dynamic programming.'''
    def forward(self, X):
        T = X.shape[0]  
        alpha = torch.zeros(T, self.num_labels)
        alpha[0] = torch.matmul(X[0], self.weights.t())


        for t in range(1, T):
            feature_score = torch.matmul(X[t], self.weights.t())
            for y_t in range(self.num_labels):
                transition_score = self.transition_weights[:, y_t]
                alpha[t, y_t] = torch.logsumexp(alpha[t-1] + transition_score, dim=0) + feature_score[y_t]

        return alpha

    '''Compute the total score for a sequence of labels y using the feature and transition weights.'''
    def compute_score(self, X, y):
        T = X.shape[0]
        score = torch.tensor(0.0)

        for t in range(T):
            score += torch.dot(self.weights[y[t]], X[t])
            if t > 0:
                score += self.transition_weights[y[t-1], y[t]]

        return score

    '''Compute the partition function Z(X) using the forward pass.'''
    def partition_function(self, X):
        alpha = self.forward(X)
        return torch.logsumexp(alpha[-1], dim=0)

    '''Compute the log-likelihood of the correct label sequence y given X.'''
    def log_likelihood(self, X, y):
        score = self.compute_score(X, y)
        partition = self.partition_function(X)
        return score - partition

    '''Viterbi algorithm for finding the most likely sequence of labels.'''
    def viterbi_decode(self, X):
        T = X.shape[0]
        dp = torch.zeros(T, self.num_labels)
        backpointer = torch.zeros(T, self.num_labels, dtype=torch.long)
        dp[0] = torch.matmul(X[0], self.weights.t())

        for t in range(1, T):
            for y_t in range(self.num_labels):
                transition_scores = dp[t-1] + self.transition_weights[:, y_t]
                dp[t, y_t] = torch.max(transition_scores) + torch.dot(self.weights[y_t], X[t])
                backpointer[t, y_t] = torch.argmax(transition_scores)

        best_seq = torch.zeros(T, dtype=torch.long)
        best_seq[T-1] = torch.argmax(dp[T-1])
        for t in range(T-2, -1, -1):
            best_seq[t] = backpointer[t+1, best_seq[t+1]]

        return best_seq

    '''Train the CRF model using Adam optimizer with negative log-likelihood loss.'''
    def fit(self, X_train, y_train, learning_rate=0.01, max_iter=100):
        optimizer = optim.Adam(self.parameters(), lr=learning_rate)

        for iteration in range(max_iter):
            total_loss = 0
            for X, y in zip(X_train, y_train):
                
                X = torch.tensor(X, dtype=torch.float32)
                y = torch.tensor(y, dtype=torch.long)
                #print(f"X shape: {X.shape}, y shape: {y.shape}")

                # Check if the input is non-empty
                if X.size(0) == 0:
                    #print(f"Empty sequence encountered at iteration {iteration}. Skipping...")
                    continue

                optimizer.zero_grad()

                loss = -self.log_likelihood(X, y)
                total_loss += loss.item()
                loss.backward()
                optimizer.step()

            print(f"Iteration {iteration + 1}, Loss: {total_loss / len(X_train)}")
    
    '''Test performance using Viterbi decoding on the testing set.'''
    def test(self, X_test, y_test):
        all_predictions = []
        all_true_labels = []

        for X, y_true in zip(X_test, y_test):
            X = torch.tensor(X, dtype=torch.float32)
            if X.size(0) == 0:
                #print(f"Empty sequence encountered at iteration {iteration}. Skipping...")
                continue
            y_pred = self.viterbi_decode(X)


            all_predictions.extend(y_pred)
            all_true_labels.extend(y_true)
            #print(f"prediction: {y_pred}")
            #print(f"actual: {y_true}")


        accuracy = accuracy_score(all_true_labels, all_predictions)
        precision, recall, f1, _ = precision_recall_fscore_support(all_true_labels, all_predictions, average='weighted')

        print(f"Accuracy: {accuracy:.4f}")
        print(f"Precision: {precision:.4f}")
        print(f"Recall: {recall:.4f}")
        print(f"F1-score: {f1:.4f}")




In [131]:
labels = ['B', 'I', 'O']
tag_map = {"B": 0, "I": 1, "O": 2}

'''Filling of X and y training and testing sets'''
X_train = []
y_train = []
for i, sentence in enumerate(sentences):
    tags = ner_data[i]
    features =  all_features[i]
    vectors = []
    for word_feature, tag in zip(features, tags):
        vector = feature_2_vec(word_feature, tag[1], pos_tags_vocabulary)
        vectors.append(vector)
    bio_tags = [tag_map[tag] for _, tag in tags]
    X_train.append(vectors)
    y_train.append(bio_tags)


X_test = []
y_test = []
for i, sentence in enumerate(test_sentences):
    tags = test_ner_data[i]
    features =  test_all_features[i]
    vectors = []
    for word_feature, tag in zip(features, tags):
        vector = feature_2_vec(word_feature, tag[1], pos_tags_vocabulary)
        vectors.append(vector)
    bio_tags = [tag_map[tag] for _, tag in tags]
    X_test.append(vectors)
    y_test.append(bio_tags)



In [132]:
'''CRF initialization and training'''
model = CRF(num_labels=3, feature_dim=6925)
model.fit(X_train, y_train)


Iteration 1, Loss: 35.299087691169255
Iteration 2, Loss: 2.5106427462803835
Iteration 3, Loss: 1.4455615592140683
Iteration 4, Loss: 0.7358594891652895
Iteration 5, Loss: 0.47195080112170623
Iteration 6, Loss: 0.3507143334846276
Iteration 7, Loss: 0.2682781991241984
Iteration 8, Loss: 0.1886402072244986
Iteration 9, Loss: 0.1322926220866297
Iteration 10, Loss: 0.05606985092163086
Iteration 11, Loss: 0.03670759421552537
Iteration 12, Loss: 0.007297157552200935
Iteration 13, Loss: 0.002884630522976032
Iteration 14, Loss: 0.002130952184599948
Iteration 15, Loss: 0.001804977483143007
Iteration 16, Loss: 0.0015772284799917585
Iteration 17, Loss: 0.0013949802156128636
Iteration 18, Loss: 0.0012460623173355368
Iteration 19, Loss: 0.0011261074529217846
Iteration 20, Loss: 0.001022559369919617
Iteration 21, Loss: 0.0009355145382743351
Iteration 22, Loss: 0.0008668169120832675
Iteration 23, Loss: 0.0007984335022854667
Iteration 24, Loss: 0.0007424864465790677
Iteration 25, Loss: 0.00069395930780

In [133]:
'''CRF testing'''
model.test(X_test, y_test)

Accuracy: 0.9938
Precision: 0.9907
Recall: 0.9938
F1-score: 0.9922
